In [2]:
# Imports
import pandas as pd
import numpy as np
from pathlib import Path
import hvplot.pandas as hv
import matplotlib.pyplot as plt
from sklearn import svm
from sklearn.svm import SVC
from sklearn.preprocessing import StandardScaler
from pandas.tseries.offsets import DateOffset
from sklearn.metrics import classification_report
import datetime as dt
from finta import TA
%matplotlib inline

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 300)

from sklearn.linear_model import LogisticRegression

In [3]:
# Import the OHLCV dataset into a Pandas Dataframe
sfzhvf_df = pd.read_csv(
    Path("../Resources/Resources/Data/Bay-Area_zhvf_uc_sfrcondo_tier_0.33_0.67_sm_sa_mon.csv")
)

# Review the DataFrame
sfzhvf_df.head(250)

Region  RegionName StateName            CountyName             CityName ForecastedDate  ForecastYoYPctChange
0      Zip       94002        CA      San Mateo County              Belmont      2/28/2022                   3.2
1      Zip       94005        CA      San Mateo County             Brisbane      2/28/2022                   3.8
2      Zip       94010        CA      San Mateo County           Burlingame      2/28/2022                   2.8
3      Zip       94014        CA      San Mateo County            Daly City      2/28/2022                   1.9
4      Zip       94015        CA      San Mateo County            Daly City      2/28/2022                   3.2
5      Zip       94018        CA      San Mateo County        Half Moon Bay      2/28/2022                   3.8
6      Zip       94019        CA      San Mateo County        Half Moon Bay      2/28/2022                   2.8
7      Zip       94020        CA      San Mateo County             La Honda      2/28/2022                   1.5
8      Zip       94021        CA      San Mateo County            Pescadero      2/28/2022                   4.8
9      Zip       94022        CA    Santa Clara County            Los Altos      2/28/2022                   3.7
10     Zip       94024        CA    Santa Clara County            Los Altos      2/28/2022                   3.9
11     Zip       94025        CA      San Mateo County           Menlo Park      2/28/2022                   2.8
12     Zip       94027        CA      San Mateo County             Atherton      2/28/2022                   2.6
13     Zip       94028        CA      San Mateo County       Portola Valley      2/28/2022                   2.2
14     Zip       94030        CA      San Mateo County             Millbrae      2/28/2022                   1.2
15     Zip       94037        CA      San Mateo County              Montara      2/28/2022                   3.4
16     Zip       94038        CA      San Mateo County           Moss Beach      2/28/2022                   3.3
17     Zip       94040        CA    Santa Clara County        Mountain View      2/28/2022                   3.4
18     Zip       94041        CA    Santa Clara County        Mountain View      2/28/2022                   3.4
19     Zip       94043        CA    Santa Clara County        Mountain View      2/28/2022                   2.4
20     Zip       94044        CA      San Mateo County             Pacifica      2/28/2022                   3.5
21     Zip       94060        CA      San Mateo County            Pescadero      2/28/2022                   3.2
22     Zip       94061        CA      San Mateo County         Redwood City      2/28/2022                   2.8
23     Zip       94062        CA      San Mateo County         Redwood City      2/28/2022                   3.7
24     Zip       94063        CA      San Mateo County         Redwood City      2/28/2022                   3.1
25     Zip       94065        CA      San Mateo County         Redwood City      2/28/2022                   1.8
26     Zip       94066        CA      San Mateo County            San Bruno      2/28/2022                   2.4
27     Zip       94070        CA      San Mateo County           San Carlos      2/28/2022                   2.9
28     Zip       94074        CA      San Mateo County         San Gregorio      2/28/2022                   1.4
29     Zip       94080        CA      San Mateo County  South San Francisco      2/28/2022                   3.5
30     Zip       94085        CA    Santa Clara County            Sunnyvale      2/28/2022                   3.4
31     Zip       94086        CA    Santa Clara County            Sunnyvale      2/28/2022                   3.2
32     Zip       94087        CA    Santa Clara County            Sunnyvale      2/28/2022                   3.1
33     Zip       94089        CA    Santa Clara County            Sunnyvale      2/28/2022                   4.1
34     Zip       94102        CA  San Francisco C

In [4]:
# Import the OHLCV dataset into a Pandas Dataframe
sfzhvi_df = pd.read_csv(
    Path("../Resources/Data/Bay-Area_Zip_zhvi_uc_sfrcondo_tier_0.33_0.67_sm_sa_mon.csv")
)

# Review the DataFrame
sfzhvi_df.head(250)

RegionID  SizeRank  RegionName RegionType StateName State                 City                           Metro            CountyName  1/31/1996  2/29/1996  3/31/1996  4/30/1996  5/31/1996  6/30/1996  7/31/1996  8/31/1996  9/30/1996  10/31/1996  11/30/1996  12/31/1996  1/31/1997  2/28/1997  \
0       97564        13       94109        Zip        CA    CA        San Francisco   San Francisco-Oakland-Hayward  San Francisco County   333727.0   332205.0   331788.0   330713.0   330535.0   330277.0   330447.0   331116.0   332377.0    333532.0    335011.0    336512.0   339376.0   342975.0   
1       97771        40       94565        Zip        CA    CA            Pittsburg   San Francisco-Oakland-Hayward   Contra Costa County        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN        NaN         NaN         NaN         NaN        NaN        NaN   
2       97711        88       94501        Zip        CA    CA              Alameda   San Francisco-Oakland-Hayward        Alameda County   183651.0   182684.0   182409.0   181685.0   181500.0   180861.0   180260.0   179867.0   179891.0    180381.0    180869.0    181603.0   182117.0   183221.0   
3       97565        94       94110        Zip        CA    CA        San Francisco   San Francisco-Oakland-Hayward  San Francisco County   285314.0   283786.0   282878.0   281548.0   280920.0   280286.0   279710.0   280674.0   282418.0    284123.0    285102.0    286893.0   289953.0   294092.0   
4       97743       231       94536        Zip        CA    CA              Fremont   San Francisco-Oakland-Hayward        Alameda County   202048.0   201616.0   201610.0   201552.0   201948.0   202098.0   202230.0   202532.0   203269.0    204486.0    205632.0    206850.0   207674.0   209021.0   
5       97991       274       95123        Zip        CA    CA             San Jose  San Jose-Sunnyvale-Santa Clara    Santa Clara County   199719.0   199149.0   198988.0   198670.0   198752.0   198886.0   199087.0   199671.0   200411.0    201601.0    203071.0    204881.0   207015.0   209344.0   
6       97940       306       95035        Zip        CA    CA             Milpitas  San Jose-Sunnyvale-Santa Clara    Santa Clara County   230694.0   229825.0   229360.0   228470.0   228023.0   227867.0   227836.0   228248.0   228681.0    229585.0    230800.0    232379.0   234362.0   236578.0   
7       97751       314       94544        Zip        CA    CA              Hayward   San Francisco-Oakland-Hayward        Alameda County   158629.0   157990.0   157912.0   157731.0   157981.0   157972.0   157861.0   157898.0   158129.0    158540.0    158884.0    159282.0   159320.0   159750.0   
8       97774       339       94568        Zip        CA    CA               Dublin   San Francisco-Oakland-Hayward        Alameda County   245815.0   245176.0   245075.0   244804.0   244939.0   244838.0   244663.0   244697.0   244929.0    245913.0    246829.0    247861.0   248128.0   248880.0   
9       97952       341       95051        Zip        CA    CA          Santa Clara  San Jose-Sunnyvale-Santa Clara    Santa Clara County   271915.0   270949.0   270675.0   270097.0   269969.0   269915.0   269804.0   270240.0   270631.0    271844.0    273634.0    275955.0   278781.0   281981.0   
10      97717       375       94509        Zip        CA    CA              Antioch   San Francisco-Oakland-Hayward   Contra Costa County    83813.0    83358.0    83263.0    83014.0    82972.0    82792.0    82596.0    82586.0    82727.0     82874.0     83066.0     83296.0    83486.0    83821.0   
11      97576       391       94122        Zip        CA    CA        San Francisco   San Francisco-Oakland-Hayward  San Francisco County   298437.0   297660.0   297334.0   296636.0   296077.0   295662.0   295043.0   295505.0   296165.0    297934.0    299835.0    302114.0   304649.0   307272.0   
12      97748       442       94541        Zip        CA    CA              Hayward   San Francisco-Oakland-Hayward        Alameda 